In [1]:
from IPython.display import Markdown as md
from IPython.display import display, HTML
import pandas as pd
import numpy as np
import ipywidgets as widgets
from pathlib import Path
from datetime import datetime
from recopytex import flat_df_students, pp_q_scores
from datetime import datetime


import chart_studio.plotly as py
import plotly.graph_objects as go
import plotly.figure_factory as ff

from plotly.offline import iplot, init_notebook_mode
init_notebook_mode()

In [2]:
tribe = "ES"
assessment = "ds2"
date = "14/10/19"
csv_file = Path(f"../{tribe}/191014_{assessment}.csv")

In [3]:
# Parameters
tribe = "2GT6"
assessment = "Ds3"
date = "22/11/21"
csv_file = "/media/documents/Cours/2021-2022/Notes/2GT6/211122_DS3.csv"


In [4]:
date = datetime.strptime(date, "%d/%m/%y")
output_path = Path(csv_file[:-4])
print(output_path)

/media/documents/Cours/2021-2022/Notes/2GT6/211122_DS3


In [5]:
if date is None:
    display(md(f"# {assessment} pour {tribe}"))
else:
    display(md(f"# {assessment} ({date:%y/%m/%d}) pour {tribe}"))

# Ds3 (21/11/22) pour 2GT6

In [22]:
stack_scores = pd.read_csv(csv_file, encoding="UTF8")
#comments = stack_scores.iloc[0]
#stack_scores.drop([0], inplace=True)
scores = flat_df_students(stack_scores).dropna(subset=["Score"])
scores = pp_q_scores(scores)
#scores.head()
#comments.drop()

In [45]:
exercises_scores = scores.groupby(["Exercice", "Eleve"]).agg({"Note": "sum", "Bareme": "sum"})

In [61]:
exercises_scores.head()

Note  Bareme
Exercice   Eleve                         
Exercice 1 ABOUHAFS Yasmine  2.00     2.0
           AKEAZI Hafsa      2.00     2.0
           AZIZ Nihal        2.00     2.0
           BARDOUSSE Yanis   1.33     2.0
           BILLET Simon      2.00     2.0

In [46]:
assessment_scores = scores.groupby(["Eleve"]).agg({"Note": "sum", "Bareme": "sum"})

In [47]:
scores.columns

Index(['Nom', 'Trimestre', 'Date', 'Exercice', 'Question', 'Competence',
       'Domaine', 'Commentaire', 'Est_nivele', 'Bareme', 'Eleve', 'Score',
       'Note', 'Niveau', 'Normalise'],
      dtype='object')

In [82]:
domain_scores = scores.groupby(["Eleve", "Domaine"]).agg({"Note": "sum", "Bareme": "sum"})
domain_scores["Normalized"] = domain_scores["Note"] / domain_scores["Bareme"]

In [74]:
#domain_scores

In [83]:
competence_scores = scores.groupby(["Eleve", "Competence"]).agg({"Note": "sum", "Bareme": "sum"})
competence_scores["Normalized"] = competence_scores["Note"] / competence_scores["Bareme"]

In [84]:
competence_scores.tail()

Note  Bareme  Normalized
Eleve         Competence                           
ZERDOUNI Adam Chercher     0.67     1.0        0.67
              Communiquer  0.67     1.0        0.67
              Modéliser    1.00     1.0        1.00
              Raisonner    2.67     5.0        0.53
              Représenter  4.66     8.0        0.58

### Bilans personnalisés

In [85]:
import pytex
#scores.head()

In [86]:
datas = {
    "assessment": {
        "name": assessment,
        "date": date
    },
    #"exercises": scores["Exercice"].unique(),
    #"questions": scores[["Exercice", 'Question', 'Competence', 'Domaine', 'Commentaire', 'Bareme', 'Est_nivele']],
    "eleves": {}
}
for e in scores["Eleve"].unique():
    edatas =  {
        "e": e,
        "assessment": assessment_scores.loc[e],
        "exercices": exercises_scores.xs(e, level="Eleve"),        "exercices": exercises_scores.xs(e, level="Eleve"),
        "domains": domain_scores.xs(e, level="Eleve"),
        "competences": competence_scores.xs(e, level="Eleve"),
        "exscores": {}
    }
    for i, ex in edatas["exercices"].iterrows():
        edatas["exscores"][i] = scores.loc[(scores.Exercice==i) & (scores.Eleve==e)]
    datas["eleves"][e] = edatas

In [125]:
score_template = r"""
\documentclass[a5paper,10pt]{article}
\usepackage{fullpage}
\usepackage{booktabs}
\usepackage{longtable}
\usepackage{tikz}
\usepackage{multicol}

\usepackage{geometry}
\geometry{left=10mm,right=10mm, top=10mm}

\renewcommand{\arraystretch}{1}
\setlength{\columnseprule}{0pt}

\pagestyle{empty}


\begin{document}


    \section*{\Var{assessment.name} \hfill \Var{e} \hfill \Var{sc.assessment.Note}/\Var{sc.assessment.Bareme}}
    %- for i,ex in sc.exercices.iterrows() 
        \subsection*{\Var{i}: \hfill \Var{ex.Note} / \Var{ex.Bareme}}
        \begin{center}
        \Var{sc.exscores[i].to_latex(index=False, columns=["Question", "Domaine", "Commentaire", "Note", "Bareme"])}
        \end{center}
    %- endfor
 
     \subsection*{Compétences}
     \begin{multicols}{2}
    %- for i,dom in sc.competences.iterrows()
        \noindent
        \Var{i} \hfill
        \begin{tikzpicture}[scale=0.7]
            \draw [](0,0) rectangle (3, 1);
            \draw [fill=black!20] (0, 0) rectangle (\Var{dom.Normalized*3}, 1);
        \end{tikzpicture}
        \hfill
        %\Var{dom.Normalized}
        
    %- endfor
    \end{multicols}

\end{document}
"""

In [126]:
tpl = pytex.texenv.from_string(score_template)

for e,sc in datas['eleves'].items():
    reportfilename = f"{date:%y%m%d}_{assessment}_{e}.tex"
    with open(output_path / reportfilename, "w") as f:
        f.write(tpl.render(sc=sc, e=e,**datas))
    print(f"Wrote {reportfilename}")
    pytex.pdflatex(reportfilename)

Wrote 211122_Ds3_ABOUHAFS Yasmine.tex
Wrote 211122_Ds3_AKEAZI Hafsa.tex
Wrote 211122_Ds3_AZIZ Nihal.tex
Wrote 211122_Ds3_BARDOUSSE Yanis.tex
Wrote 211122_Ds3_BILLET Simon.tex
Wrote 211122_Ds3_BOUAFIA Lina.tex
Wrote 211122_Ds3_DESGLENE Anthony.tex
Wrote 211122_Ds3_DROUOT Marine.tex
Wrote 211122_Ds3_FLACHERON Maylie.tex
Wrote 211122_Ds3_GARCIA MORENO Alberto.tex
Wrote 211122_Ds3_GNUI Kadia.tex
Wrote 211122_Ds3_GOSSET Jules.tex
Wrote 211122_Ds3_GOUGEAUD William.tex
Wrote 211122_Ds3_GRISON Jade.tex
Wrote 211122_Ds3_HAMIOT Anaïs.tex
Wrote 211122_Ds3_HAMMOUDI Lyna.tex
Wrote 211122_Ds3_JOUNEAU Cassandra.tex
Wrote 211122_Ds3_LAFUMAS Flora.tex
Wrote 211122_Ds3_MERLE Yannis.tex
Wrote 211122_Ds3_MONET--BRIFFOD Antonin.tex
Wrote 211122_Ds3_MONOD Mélissa.tex
Wrote 211122_Ds3_MULTIN Théo.tex
Wrote 211122_Ds3_NEIVA Diego.tex
Wrote 211122_Ds3_PETIT Aidan.tex
Wrote 211122_Ds3_PRAT Lilou.tex
Wrote 211122_Ds3_RINALDI Gianni.tex
Wrote 211122_Ds3_RIVERA--DRENEUC Kerly.tex
Wrote 211122_Ds3_ROSA DOS SANTOS A

## Envoie des bilans par mail

In [127]:
mailfrom = "benjamin.bertrand@ac-lyon.fr"
subject = f"Bian du devoir {assessment}"
message = """Bonsoir,
En pièce jointe, vous trouverez un document détaillant la note du devoir.
B.Bertrand
"""
print(subject)
print(message)

Bian du devoir Ds3
Bonsoir,
En pièce jointe, vous trouverez un document détaillant la note du devoir.
B.Bertrand



In [128]:
import smtplib
import os
import sys
from email.message import EmailMessage
import mimetypes
import time
import random

In [129]:
def build_msg(subj, to_addr, from_addr, body, att):
    msg = EmailMessage()
    msg["Subject"] = subj
    msg["To"] = to_addr
    #msg["To"] = "lafrite26@gmail.com"
    msg["From"] = from_addr
    msg.set_content(body)

    if att != []:
        ctype, encoding = mimetypes.guess_type(att)
        if ctype is None or encoding is not None:
            ctype = 'application/octet-stream'
        maintype, subtype = ctype.split('/', 1)
        with open(att, "rb") as f:
            msg.add_attachment(f.read(),
                maintype=maintype,
                subtype=subtype,
                filename=att.name)
    return msg


In [130]:
send = 0
fake = 1

In [131]:
if send:
    if fake:
        server = smtplib.SMTP("localhost", 8025)
        server.ehlo()
    else:
        server = smtplib.SMTP("smtps.ac-lyon.fr", 587)
        server.ehlo()
        server.starttls()
        server.ehlo()
        server.login("bbertrand", os.popen("pass Prof/Lyon/bbertrand").read()[:-1])   

In [132]:
try:
    eleves_data = pd.read_csv(f"../../{tribe}.csv")
except FileNotFoundError:
    try:
        eleves_data = pd.read_csv(f"../{tribe}.csv")
    except FileNotFoundError:
        eleves_data = pd.read_csv(f"{tribe}.csv")
eleves_data.fillna("", inplace=True)
#eleves_data

In [133]:
for e in eleves_data.iterrows():
    reportfilename = Path(f"{date:%y%m%d}_{assessment}_{e[1]['Nom']}.pdf")
    try:
        assert reportfilename.exists()
    except:
        print(f"Pas de rapport pour {e[1]['Nom']}")
    else:
        if e[1]["mail"] != "":
            if send:
                msg = build_msg(subject, e[1]["mail"], mailfrom, message, reportfilename)
                server.send_message(msg)
                print(f"\tBilan envoyé à {e[1]['Nom']}")
        else:
            print(f"Pas de mail pour {e[1]['Nom']}")
            

	Bilan envoyé à ABOUHAFS Yasmine
Pas de mail pour AKEAZI Hafsa
Pas de mail pour AZIZ Nihal
	Bilan envoyé à BARDOUSSE Yanis
	Bilan envoyé à BILLET Simon
Pas de mail pour BOUAFIA Lina
	Bilan envoyé à DESGLENE Anthony
	Bilan envoyé à DROUOT Marine
	Bilan envoyé à FLACHERON Maylie
	Bilan envoyé à GARCIA MORENO Alberto
	Bilan envoyé à GNUI Kadia
	Bilan envoyé à GOSSET Jules
	Bilan envoyé à GOUGEAUD William
Pas de mail pour GRISON Jade
	Bilan envoyé à HAMIOT Anaïs
	Bilan envoyé à HAMMOUDI Lyna
	Bilan envoyé à JOUNEAU Cassandra
	Bilan envoyé à LAFUMAS Flora
Pas de mail pour MERLE Yannis
	Bilan envoyé à MONET--BRIFFOD Antonin
	Bilan envoyé à MONOD Mélissa
	Bilan envoyé à MULTIN Théo
	Bilan envoyé à NEIVA Diego
Pas de rapport pour PERROTIN Léonie
Pas de mail pour PETIT Aidan
	Bilan envoyé à PRAT Lilou
	Bilan envoyé à RINALDI Gianni
Pas de mail pour RIVERA--DRENEUC Kerly
	Bilan envoyé à ROSA DOS SANTOS Andréa
	Bilan envoyé à TAIBI Shaima
	Bilan envoyé à TELEGONE Angie
Pas de mail pour ZERDOUNI A